<a href="https://colab.research.google.com/github/lenam2132002/Transformer-Explainability/blob/main1/bert_ex_for_model_6_labels.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone -b main1 https://github.com/lenam2132002/Transformer-Explainability.git

Cloning into 'Transformer-Explainability'...
remote: Enumerating objects: 413, done.
remote: Counting objects: 100% (36/36), done.
remote: Compressing objects: 100% (26/26), done.
remote: Total 413 (delta 15), reused 24 (delta 8), pack-reused 377
Receiving objects: 100% (413/413), 3.87 MiB | 25.92 MiB/s, done.
Resolving deltas: 100% (206/206), done.


In [2]:
!pip install captum

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 15.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 24.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 25.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 16.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━

In [3]:
%cd /content/Transformer-Explainability

/content/Transformer-Explainability


In [4]:
from transformers import BertTokenizer
from BERT_explainability.modules.BERT.ExplanationGenerator import Generator
from BERT_explainability.modules.BERT.BertForSequenceClassification import BertForSequenceClassification
from transformers import BertTokenizer
from BERT_explainability.modules.BERT.ExplanationGenerator import Generator
from transformers import AutoTokenizer

from captum.attr import visualization
import torch
from transformers import AutoTokenizer, AutoModelForMaskedLM, AutoModel
from transformers import BertTokenizer, BertModel

In [5]:
model = BertForSequenceClassification.from_pretrained("jackaduma/SecBERT", num_labels=6).to("cuda")
model.eval()
tokenizer = AutoTokenizer.from_pretrained('jackaduma/SecBERT')
# initialize the explanations generator


classifications = ["000 - Normal", '126 - Path Traversal',
               '242 - Code Injection', '274 - HTTP Verb Tampering',
               '66 - SQL Injection', '88 - OS Command Injection']
explanations = Generator(model)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/467 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/336M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at jackaduma/SecBERT and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


vocab.txt:   0%|          | 0.00/378k [00:00<?, ?B/s]

In [6]:
# prompt: connect to gg drive

from google.colab import drive
drive.mount('/content/gdrive')


Mounted at /content/gdrive


In [7]:
checkpoint = torch.load('/content/gdrive/MyDrive/Code_Injection_Dataset/best_model_6labels.pt')

In [8]:
dict = checkpoint['state_dict']
dict1 = dict.copy()
for name in dict.keys():
    name_new = name.replace('bert_model', 'bert')
    dict1[name_new] = dict[name]
    del dict1[name]

In [9]:
dict2 = model.state_dict()
# dict2["bert.embeddings.position_ids"]

In [10]:
dict1["bert.embeddings.position_embeddings.weight"] = dict["bert_model.embeddings.position_embeddings.weight"]
dict1["bert.embeddings.word_embeddings.weight"] = dict["bert_model.embeddings.word_embeddings.weight"]
dict1["classifier.weight"] = dict["linear.weight"]
dict1["classifier.bias"] = dict["linear.bias"]
dict1["bert.embeddings.position_ids"] = dict2["bert.embeddings.position_ids"]

In [11]:
model.load_state_dict(dict1)

<All keys matched successfully>

In [12]:
import pandas as pd

In [18]:
normal = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/000.csv')


In [19]:
count = 0
for index, row in normal.iterrows():
    if index > 10:
        break
    # if index <= 10:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

000 - Normal
[('[CLS]', 0.0), ('get', 0.0), ('/', 0.9356299042701721), ('[SEP]', 1.0)]


/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.38527247309684753), ('blog', 0.04108406603336334), ('/', 0.17483685910701752), ('index', 0.03218269720673561), ('.', 0.03432620316743851), ('php', 0.02236943133175373), ('/', 0.2802586853504181), ('2020', 0.1084015965461731), ('/', 0.1715889275074005), ('04', 0.06460774689912796), ('/', 0.10837946832180023), ('04', 0.04372565075755119), ('/', 0.05097191780805588), ('vol', 0.013571112416684628), ('##upt', 0.019376488402485847), ('##atu', 0.016526956111192703), ('##m', 0.010048878379166126), ('-', 0.01952430047094822), ('repre', 0.0002791851293295622), ('##hen', 0.001402774709276855), ('##der', 0.011828623712062836), ('##it', 0.006599586922675371), ('-', 0.03223433718085289), ('ma', 0.014507235959172249), ('##ior', 0.008417344652116299), ('##es', 0.0024504682514816523), ('-', 0.024011723697185516), ('ab', 0.004466221667826176), ('-', 0.017325079068541527), ('sequ', 0.0038804158102720976), ('##i', 0.02278902940452099), ('-', 0.0158838964

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.2137824296951294), ('/', -0.010729064233601093), ('blog', -0.040987640619277954), ('/', -0.001939126173965633), ('xmlrpc', -0.04450560733675957), ('.', -0.0), ('php', -0.08688294142484665), ('?', -1.0), ('rs', -0.36760661005973816), ('##d', -0.7329966425895691), ('[SEP]', -0.010899742133915424)]


000 - Normal
[('[CLS]', 0.0), ('get', 0.9375236630439758), ('/', 0.8564178347587585), ('blog', 0.09984881430864334), ('/', 0.22380398213863373), ('index', 0.01865287870168686), ('.', 0.043998073786497116), ('php', 0.029168518260121346), ('/', 0.23909486830234528), ('2020', 0.11389486491680145), ('/', 0.16174203157424927), ('04', 0.042460788041353226), ('/', 0.07815674692392349), ('04', 0.04177847504615784), ('/', 0.05588826537132263), ('nih', 0.01489597000181675), ('##il', 0.013937239535152912), ('-', 0.036545395851135254), ('ten', 0.0), ('##et', 0.00985301285982132), ('##ur', 0.0028666751459240913), ('-', 0.03826138749718666), ('et', 0.0335547961294651), ('-', 0.031146777793765068), ('ad', 0.0008040748070925474), ('-', 0.03631601482629776), ('in', 0.024168333038687706), ('-', 0.03248750790953636), ('dol', 0.007369023747742176), ('##ores', 0.07215790450572968), ('/', 0.3217941224575043), ('[SEP]', 1.0)]


...

000 - Normal
[('[CLS]', 0.0), ('get', 0.827971875667572), ('/', 0.7590953707695007), ('blog', 0.20681442320346832), ('/', 0.33103129267692566), ('index', 0.031585559248924255), ('.', 0.02411649562418461), ('php', 0.011818560771644115), ('/', 0.16365757584571838), ('comments', 0.0), ('/', 0.04252535477280617), ('feed', 0.03338583558797836), ('/', 0.9511666297912598), ('[SEP]', 1.0)]


000 - Normal
[('[CLS]', 0.0), ('get', 0.827971875667572), ('/', 0.7590953707695007), ('blog', 0.20681442320346832), ('/', 0.33103129267692566), ('index', 0.031585559248924255), ('.', 0.02411649562418461), ('php', 0.011818560771644115), ('/', 0.16365757584571838), ('comments', 0.0), ('/', 0.04252535477280617), ('feed', 0.03338583558797836), ('/', 0.9511666297912598), ('[SEP]', 1.0)]


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.7288148403167725), ('blog', 0.05079251155257225), ('/', 0.21697482466697693), ('index', 0.029430309310555458), ('.', 0.040813010185956955), ('php', 0.02205183357000351), ('/', 0.25165459513664246), ('2020', 0.09585192054510117), ('/', 0.15528637170791626), ('04', 0.04777644947171211), ('/', 0.12488717585802078), ('04', 0.03192077949643135), ('/', 0.05540217086672783), ('tempor', 0.010307678021490574), ('##e', 0.030929604545235634), ('-', 0.05249256268143654), ('od', 0.005613185465335846), ('##it', 0.007350863888859749), ('-', 0.09302536398172379), ('cup', 0.004743034020066261), ('##idi', 0.002813937608152628), ('##tate', 0.0), ('-', 0.09986615180969238), ('vol', 0.004280662629753351), ('##upt', 0.0032069936860352755), ('##as', 0.0012162949424237013), ('-', 0.08040988445281982), ('la', 0.017668960615992546), ('##uda', 0.0013309468049556017), ('##nt', 0.006892605219036341), ('##ium', 0.012073248624801636), ('-', 0.08081907778978348), ('

000 - Normal
[('[CLS]', 0.0), ('get', 0.6118040680885315), ('/', 0.725074827671051), ('blog', 0.06381276249885559), ('/', 0.20656903088092804), ('index', 0.026135584339499474), ('.', 0.04491310194134712), ('php', 0.032735228538513184), ('/', 0.21121762692928314), ('2020', 0.11330069601535797), ('/', 0.08088663965463638), ('04', 0.06163020431995392), ('/', 0.057586681097745895), ('04', 0.049273017793893814), ('/', 0.03750056400895119), ('hi', 0.008410963229835033), ('##c', 0.012643648311495781), ('-', 0.02297159470617771), ('por', 0.0), ('##ro', 0.002934922929853201), ('-', 0.033473413437604904), ('nih', 6.930145173100755e-05), ('##il', 6.97430095897289e-06), ('-', 0.025001486763358116), ('non', 0.001616671564988792), ('-', 0.03564182668924332), ('rer', 0.014470666646957397), ('##um', 0.1329653561115265), ('/', 0.49762335419654846), ('[SEP]', 1.0)]


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.861062228679657), ('blog', 0.09293100237846375), ('/', 0.28895896673202515), ('wp', 0.08099480718374252), ('-', 0.06843370199203491), ('content', 0.03500736504793167), ('/', 0.21103641390800476), ('uploads', 0.07184641808271408), ('/', 0.3222929537296295), ('2020', 0.07315677404403687), ('/', 0.42360228300094604), ('04', 0.04584978520870209), ('/', 0.062331367284059525), ('cro', 0.04236666485667229), ('##pped', 0.026925036683678627), ('-', 0.024733377620577812), ('587', 0.027920590713620186), ('##d6', 0.011373454704880714), ('##9f', 0.12620097398757935), ('##7', 0.023454321548342705), ('-', 0.05263768509030342), ('b2', 0.005816956982016563), ('##e2', 0.006234018597751856), ('-', 0.051054079085588455), ('363', 0.014006839133799076), ('##b', 0.008617503568530083), ('-', 0.05228786915540695), ('b7', 0.010599824599921703), ('##6a', 0.012358888983726501), ('-', 0.04113098606467247), ('5f', 0.02530013583600521), ('##d0', 0.00137998908758163

In [21]:
path_travelsal = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/126.csv')
for index, row in path_travelsal.iterrows():
    if index > 1010:
        break
    if index <= 1000:
        continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.11712200194597244), ('/', -0.03751807659864426), ('blog', -0.021837253123521805), ('/', -0.029802409932017326), ('index', -0.028804102912545204), ('.', -0.05726766586303711), ('php', -0.02295719087123871), ('/', -0.020001834258437157), ('2020', -0.022352896630764008), ('/', -0.017190933227539062), ('03', -0.01630232110619545), ('/', -0.030077289789915085), ('.', -0.425700306892395), ('.', -0.7717921733856201), ('%', -0.2656601071357727), ('2f', -0.1517566740512848), ('.', -0.8870986700057983), ('.', -0.995913565158844), ('%', -0.19494090974330902), ('2f', -0.11867548525333405), ('.', -0.7821119427680969), ('.', -0.8272891640663147), ('%', -0.2439047247171402), ('2f', -0.17819303274154663), ('.', -0.7851148247718811), ('.', -1.0), ('%', -0.2504652142524719), ('2f', -0.12076488882303238), ('.', -0.6982212662696838), ('.', -0.798364520072937), ('%', -0.13212382793426514), ('2f', -0.10137315094470978), ('.', -0.48101744055747986), ('.', -0.

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.024370631203055382), ('/', -0.03142785653471947), ('blog', -0.025513295084238052), ('/', -0.06954001635313034), ('.', -0.4384651780128479), ('.', -0.5939334630966187), ('%', -0.10648252069950104), ('2f', -0.12334956228733063), ('.', -0.7374179363250732), ('.', -0.8290250897407532), ('%', -0.139823317527771), ('2f', -0.14806896448135376), ('.', -0.7076903581619263), ('.', -0.7945428490638733), ('%', -0.20478278398513794), ('2f', -0.16818633675575256), ('.', -1.0), ('.', -0.9964243173599243), ('%', -0.16313570737838745), ('2f', -0.13494139909744263), ('.', -0.7925055027008057), ('.', -0.7153845429420471), ('%', -0.19448363780975342), ('2f', -0.21058033406734467), ('.', -0.803327202796936), ('.', -0.8850560784339905), ('%', -0.18546703457832336), ('2f', -0.12833337485790253), ('.', -0.7222491502761841), ('.', -0.7462772130966187), ('%', -0.11166895925998688), ('2f', -0.09895452111959457), ('.', -0.5197012424468994), ('.', -0.62491679191589

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.20803885161876678), ('/', -0.06061651557683945), ('blog', -0.04518779739737511), ('/', -0.06152879819273949), ('index', -0.09891855716705322), ('.', -0.17850741744041443), ('php', -0.056734099984169006), ('/', -0.04089345037937164), ('2020', -0.042193181812763214), ('/', -0.051081787794828415), ('03', -0.05635625869035721), ('/', -0.08656071126461029), ('.', -0.786518931388855), ('.', -1.0), ('%', -0.23893220722675323), ('5c', -0.2857837677001953), ('.', -0.7830076217651367), ('.', -0.9267171621322632), ('%', -0.20965903997421265), ('5c', -0.1796882599592209), ('.', -0.5387839674949646), ('.', -0.6975613832473755), ('%', -0.19823551177978516), ('5c', -0.25567978620529175), ('.', -0.6844694018363953), ('.', -0.9071547389030457), ('%', -0.20679138600826263), ('5c', -0.20791321992874146), ('.', -0.48145028948783875), ('.', -0.7291992902755737), ('%', -0.14013856649398804), ('5c', -0.2563806176185608), ('.', -0.4619438946247101), ('.', -0.7

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.1757594347000122), ('/', -0.06669413298368454), ('blog', -0.047653499990701675), ('/', -0.0940806195139885), ('.', -0.7605113387107849), ('.', -1.0), ('%', -0.21139809489250183), ('5c', -0.23812302947044373), ('.', -0.5358402132987976), ('.', -0.9416600465774536), ('%', -0.24866411089897156), ('5c', -0.28584063053131104), ('.', -0.6308618187904358), ('.', -0.8351005911827087), ('%', -0.22382034361362457), ('5c', -0.23972944915294647), ('.', -0.5550731420516968), ('.', -0.7135102152824402), ('%', -0.20240448415279388), ('5c', -0.16941584646701813), ('.', -0.36551904678344727), ('.', -0.5299726724624634), ('%', -0.1915132701396942), ('5c', -0.23336227238178253), ('.', -0.49267423152923584), ('.', -0.68853759765625), ('%', -0.1958114504814148), ('5c', -0.1902889460325241), ('.', -0.35914933681488037), ('.', -0.5183262228965759), ('%', -0.12921983003616333), ('5c', -0.21944734454154968), ('.', -0.3546289801597595), ('.', -0.5512832999229431

...

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.01989028789103031), ('/', -0.023302949965000153), ('blog', -0.01757217012345791), ('/', -0.030196644365787506), ('%', -0.059012897312641144), ('2f', -0.0893530622124672), ('.', -0.39099615812301636), ('.', -0.47365602850914), ('%', -0.1115136593580246), ('2f', -0.10668712109327316), ('.', -0.7262264490127563), ('.', -0.9035069942474365), ('%', -0.18393662571907043), ('2f', -0.09136674553155899), ('.', -0.6567986607551575), ('.', -1.0), ('%', -0.21588456630706787), ('2f', -0.12303473055362701), ('.', -0.5952997803688049), ('.', -0.630443811416626), ('%', -0.15409961342811584), ('2f', -0.14429737627506256), ('.', -0.596136212348938), ('.', -0.8208302855491638), ('%', -0.1772657036781311), ('2f', -0.12211353331804276), ('.', -0.5318315029144287), ('.', -0.5578225255012512), ('%', -0.1322614997625351), ('2f', -0.07882507890462875), ('.', -0.5092914700508118), ('.', -0.5680035948753357), ('%', -0.07282794266939163), ('2f', -0.055645603686571

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.17900578677654266), ('/', -0.06287902593612671), ('blog', -0.042881954461336136), ('/', -0.060568951070308685), ('index', -0.09946659952402115), ('.', -0.1776210218667984), ('php', -0.05121360719203949), ('/', -0.03803715482354164), ('2020', -0.039893556386232376), ('/', -0.04708791896700859), ('03', -0.038704439997673035), ('/', -0.06347060203552246), ('%', -0.1775667816400528), ('5c', -0.15815469622612), ('.', -0.547269344329834), ('.', -1.0), ('%', -0.21539637446403503), ('5c', -0.28139016032218933), ('.', -0.520808756351471), ('.', -0.6467354893684387), ('%', -0.15829110145568848), ('5c', -0.2579643726348877), ('.', -0.6332785487174988), ('.', -0.9836563467979431), ('%', -0.25382184982299805), ('5c', -0.3361232280731201), ('.', -0.6199696660041809), ('.', -0.727477490901947), ('%', -0.15968918800354004), ('5c', -0.19718299806118011), ('.', -0.4563961923122406), ('.', -0.8062072396278381), ('%', -0.15756045281887054), ('5c', -0.25264

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.10796009749174118), ('/', -0.05101509019732475), ('blog', -0.03163864463567734), ('/', -0.06525351852178574), ('%', -0.11226067692041397), ('5c', -0.21818740665912628), ('.', -0.49136069416999817), ('.', -0.6366003155708313), ('%', -0.14683084189891815), ('5c', -0.1836550235748291), ('.', -0.7240861058235168), ('.', -1.0), ('%', -0.24702177941799164), ('5c', -0.1588674634695053), ('.', -0.4823700189590454), ('.', -0.8276699185371399), ('%', -0.16764770448207855), ('5c', -0.17186254262924194), ('.', -0.3567673861980438), ('.', -0.4624525010585785), ('%', -0.12248317897319794), ('5c', -0.1511911153793335), ('.', -0.4317527413368225), ('.', -0.6763743758201599), ('%', -0.17766718566417694), ('5c', -0.23738864064216614), ('.', -0.43188202381134033), ('.', -0.5163815021514893), ('%', -0.12193984538316727), ('5c', -0.1343642771244049), ('.', -0.3326265811920166), ('.', -0.5447043180465698), ('%', -0.11324937641620636), ('5c', -0.1865685880184

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.08951951563358307), ('/', -0.0447278656065464), ('blog', -0.029032232239842415), ('/', -0.046925559639930725), ('index', -0.05869416892528534), ('.', -0.0715632438659668), ('php', -0.09797929972410202), ('/', -0.03511097654700279), ('2020', -0.03238832205533981), ('/', -0.038082901388406754), ('03', -0.1280945986509323), ('/', -0.03558379039168358), ('22', -0.296307772397995), ('/', -0.06768777221441269), ('.', -0.5733320713043213), ('.', -0.9636619091033936), ('%', -0.31512153148651123), ('2f', -0.1577066034078598), ('.', -0.5472813844680786), ('.', -0.6204547882080078), ('%', -0.21745361387729645), ('2f', -0.17517922818660736), ('.', -0.8549761176109314), ('.', -1.0), ('%', -0.27974995970726013), ('2f', -0.13677483797073364), ('.', -0.4547482430934906), ('.', -0.5470455288887024), ('%', -0.1284879595041275), ('2f', -0.0818597599864006), ('.', -0.40502095222473145), ('.', -0.3920134902000427), ('%', -0.0564076192677021), ('2f', -0.0497

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.0662834644317627), ('/', -0.048630766570568085), ('blog', -0.02952190488576889), ('/', -0.049380019307136536), ('index', -0.06785783171653748), ('.', -0.07635698467493057), ('php', -0.10876248776912689), ('/', -0.0389464795589447), ('2020', -0.032404035329818726), ('/', -0.03970300033688545), ('03', -0.15556496381759644), ('/', -0.03724020719528198), ('22', -0.36646848917007446), ('/', -0.060868702828884125), ('%', -0.20417749881744385), ('2f', -0.14698338508605957), ('.', -0.869642972946167), ('.', -1.0), ('%', -0.2088686227798462), ('2f', -0.12924833595752716), ('.', -0.8390673398971558), ('.', -0.870638906955719), ('%', -0.3431447148323059), ('2f', -0.17750030755996704), ('.', -0.851590633392334), ('.', -0.8545811772346497), ('%', -0.18655671179294586), ('2f', -0.10909126698970795), ('.', -0.48667111992836), ('.', -0.569186806678772), ('%', -0.08050556480884552), ('2f', -0.07259224355220795), ('.', -0.23368415236473083), ('.', -0.305

In [22]:
code_injection = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/242.csv')
for index, row in code_injection.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


242 - Code Injection
[('[CLS]', -0.0), ('post', -0.05537935718894005), ('/', -0.03680241107940674), ('vendor', -0.16251617670059204), ('/', -0.028404876589775085), ('php', -0.12225503474473953), ('##unit', -0.011883022263646126), ('/', -0.03209169954061508), ('php', -0.049307968467473984), ('##unit', -0.0011245032073929906), ('/', -0.02383584715425968), ('src', -0.028514111414551735), ('/', -0.010014573112130165), ('util', -0.006623837165534496), ('/', -0.012125950306653976), ('php', -0.020154107362031937), ('/', -0.02173163928091526), ('eval', -0.029048219323158264), ('-', -0.004034770652651787), ('stdin', -0.0), ('.', -0.004475196357816458), ('php', -0.05014410242438316), ('<', -0.45465224981307983), ('?', -0.20169223845005035), ('=', -0.05082954466342926), ('md5', -0.1544078141450882), ('(', -0.08517607301473618), ('"', -0.08293699473142624), ('php', -0.03275657072663307), ('##unit', -0.012850272469222546), ('"', -0.7288517355918884), (')', -1.0), ('?', -0.755683422088623), ('>', -0

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.030499188229441643), ('/', -0.023848284035921097), ('?', -0.45801350474357605), ('-', -0.24941569566726685), ('d', -0.2534940242767334), ('+', -0.2234487682580948), ('allow', -0.03506903722882271), ('_', -0.029862232506275177), ('url', -0.005010172724723816), ('_', -0.03147856146097183), ('include', -0.055902015417814255), ('%', -0.40570327639579773), ('3d', -0.05757701024413109), ('##1', -0.03755391016602516), ('+', -0.38036057353019714), ('-', -0.07675893604755402), ('d', -0.1332024335861206), ('+', -0.10479188710451126), ('auto', -0.02294149622321129), ('_', -0.018103281036019325), ('prepend', -0.005586911924183369), ('_', -0.024945568293333054), ('file', -0.01075842883437872), ('%', -0.1973738670349121), ('3d', -0.05978115648031235), ('##php', -0.008837665431201458), (':', -0.009092263877391815), ('/', -0.0113555658608675), ('/', -0.01069432683289051), ('input', -0.007253128103911877), ('<', -0.0972890555858612), ('?', -0.032671041

242 - Code Injection
[('[CLS]', -0.0), ('get', -0.014121059328317642), ('/', -0.07029837369918823), ('?', -0.4757985770702362), ('p4', -0.08355456590652466), ('##yl', -0.009801358915865421), ('##04', -0.2806640565395355), ('##d3', -0.026325898244976997), ('=', -0.2379823625087738), ('<', -1.0), ('script', -0.09251519292593002), ('>', -0.24820508062839508), ('alert', -0.07626695185899734), ('(', -0.06014948710799217), ('document', -0.0), ('.', -0.07128927111625671), ('cookie', -0.03206867724657059), (')', -0.280602365732193), ('<', -0.5994272232055664), ('/', -0.06271965801715851), ('script', -0.02428857795894146), ('>', -0.08638405054807663), ('[SEP]', -0.002483092015609145)]


242 - Code Injection
[('[CLS]', -0.0), ('get', -0.12370332330465317), ('/', -0.06362175941467285), ('index', -0.06576982885599136), ('.', -0.045244887471199036), ('php', -0.033208370208740234), ('?', -0.06118036434054375), ('s', -0.0293586403131485), ('=', -0.1275087296962738), ('/', -0.0351339690387249), ('index', -0.018055342137813568), ('/', -0.01764652691781521), ('\\', -0.03852668032050133), ('x5', -0.001276020659133792), ('##ct', -0.002106198575347662), ('##hink', -0.007772920187562704), ('\\', -0.016007598489522934), ('x5', -0.0), ('##cap', -0.01577143184840679), ('##p', -0.02526465430855751), ('/', -0.012093640863895416), ('invoke', -0.032112304121255875), ('##function', -0.009661323390901089), ('&', -0.02233405038714409), ('function', -0.009521451778709888), ('=', -0.013527672737836838), ('call', -0.0016579310176894069), ('_', -0.014929685741662979), ('user', -0.006159220356494188), ('_', -0.01751876436173916), ('func', -0.006554845254868269), ('_', -0.009989950805902481), ('a

...

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.12600943446159363), ('/', -0.07903613150119781), ('blog', -0.029955293983221054), ('/', -0.07909943908452988), ('index', -0.018682459369301796), ('.', -0.01882816106081009), ('php', -0.020138390362262726), ('/', -0.03540158271789551), ('my', -0.007441752590239048), ('-', -0.011479848064482212), ('account', -0.009615716524422169), ('/', -0.020566079765558243), ('edit', -0.00024037393450271338), ('-', -0.0126678217202425), ('password', -0.00425837142392993), ('/', -0.01621532253921032), ('password', -0.00728906225413084), ('_', -0.03717069700360298), ('current', -0.007936730980873108), ('=', -0.022807110100984573), ('tn', -0.00397829432040453), ('##ce', -0.0032036672346293926), ('##qi', -0.0033971485681831837), ('##u', -0.02388009801506996), ('&', -0.024473583325743675), ('password', -0.010510609485208988), ('_', -0.030144624412059784), ('1', -0.01336263120174408), ('=', -0.08809604495763779), ('%', -0.6989405155181885), ('3c', -1.0), ('

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.1955936998128891), ('/', -0.055919524282217026), ('blog', -0.015650611370801926), ('/', -0.06334324926137924), ('index', -0.013018220663070679), ('.', -0.033204928040504456), ('php', -0.022348403930664062), ('/', -0.05118226632475853), ('my', -0.013047248125076294), ('-', -0.016876159235835075), ('account', -0.011911580339074135), ('/', -0.02399597130715847), ('edit', -0.0010382275795564055), ('-', -0.015102704986929893), ('password', -0.00978360790759325), ('/', -0.022218745201826096), ('password', -0.012519613839685917), ('_', -0.04372238367795944), ('current', -0.012994188815355301), ('=', -0.024223148822784424), ('ec', -0.011835625395178795), ('##fl', -0.008276368491351604), ('##bd', -0.021616848185658455), ('&', -0.03811774402856827), ('password', -0.016335701569914818), ('_', -0.043765854090452194), ('1', -0.01677723415195942), ('=', -0.060345884412527084), ('%', -0.572384238243103), ('22', -0.5919215083122253), ('%', -0.32954034

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.10404804348945618), ('/', -0.026556065306067467), ('blog', -0.0114488760009408), ('/', -0.028684167191386223), ('index', -0.005479749757796526), ('.', -0.0147382328286767), ('php', -0.010130060836672783), ('/', -0.014877702109515667), ('my', -0.006058217491954565), ('-', -0.005319966934621334), ('account', -0.007236336823552847), ('/', -0.007997927255928516), ('edit', -0.0), ('-', -0.00582038052380085), ('password', -0.0024066187907010317), ('/', -0.0062050484120845795), ('password', -0.0030820949468761683), ('_', -0.019227242097258568), ('current', -0.00620281184092164), ('=', -0.011816920712590218), ('dv', -0.00019929780683014542), ('##sz', -0.0009439077111892402), ('##g', -0.002343494212254882), ('&', -0.007832908071577549), ('password', -0.0035227746702730656), ('_', -0.015694988891482353), ('1', -0.006182230077683926), ('=', -0.013852888718247414), ('dv', -0.0013917264295741916), ('##sz', -0.000964887673035264), ('##g', -0.0060251

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.356716126203537), ('/', -0.05241001769900322), ('blog', -0.01481019239872694), ('/', -0.04852098971605301), ('index', -0.01916644349694252), ('.', -0.025576597079634666), ('php', -0.03273994103074074), ('/', -0.04242639243602753), ('my', -0.008854086510837078), ('-', -0.01799057237803936), ('account', -0.012910752557218075), ('/', -0.023112831637263298), ('edit', -0.005865673068910837), ('-', -0.019298648461699486), ('password', -0.004408217500895262), ('/', -0.02155960723757744), ('password', -0.004345301538705826), ('_', -0.025864144787192345), ('current', -0.005727636627852917), ('=', -0.025386527180671692), ('qb', -0.0003518434823490679), ('##iw', -0.0025692537892609835), ('##fy', -0.007578141987323761), ('&', -0.0276458989828825), ('password', -0.0035183464642614126), ('_', -0.02779589220881462), ('1', -0.005836716387420893), ('=', -0.031594764441251755), ('qb', -0.005534935276955366), ('##iw', -0.001732513657771051), ('##fy', -0.

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.09720473736524582), ('/', -0.03493332117795944), ('blog', -0.03658309951424599), ('/', -0.03799537941813469), ('index', -0.02072272077202797), ('.', -0.016738221049308777), ('php', -0.011649899184703827), ('/', -0.018042994663119316), ('my', -0.009645321406424046), ('-', -0.008277390152215958), ('account', -0.005775779485702515), ('/', -0.006724692415446043), ('edit', -0.0044974274933338165), ('-', -0.006588320713490248), ('password', -0.002994330134242773), ('/', -0.008806029334664345), ('password', -0.001773711177520454), ('_', -0.020629415288567543), ('current', -0.004048693459481001), ('=', -0.008249563165009022), ('fb', -0.005763348191976547), ('##8f', -0.0029631268698722124), ('-', -0.007738899905234575), ('es', -0.0009829732589423656), ('&', -0.007807013113051653), ('password', -0.0026365609373897314), ('_', -0.011722339317202568), ('1', -0.009721826761960983), ('=', -0.012391322292387486), ('fb', -0.005118644796311855), ('##8f'

In [23]:
HTTP_Verb_Tampering = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/274.csv')
for index, row in HTTP_Verb_Tampering.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('th', -0.4123900532722473), ('##b', -0.3175850808620453), ('##q', -0.552528977394104), ('/', -1.0), ('nan', -0.20032140612602234), ('[SEP]', -0.0)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -0.4882279634475708), ('/', -1.0), ('19', -0.054638415575027466), ('##sa', -0.0), ('##q', -0.002231227234005928), ('nan', -0.0519530288875103), ('[SEP]', -0.053962718695402145)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -0.5437328219413757), ('/', -1.0), ('icons', -0.3269472122192383), ('##vc', -0.1250748485326767), ('##cb', -0.0014795559691265225), ('##m', -0.025788603350520134), ('nan', -0.01961236260831356), ('[SEP]', -0.0)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -0.8251001238822937), ('/', -1.0), ('icons', -0.4923947751522064), ('/', -0.5964377522468567), ('ubuntu', -0.0682065412402153), ('-', -0.05979714170098305), ('logo', -0.026181340217590332), ('.', -0.00043453293619677424), ('png', -0.01158677227795124), ('##yp', -0.0026808353140950203), ('##g', -0.0), ('##dk', -0.0015263096429407597), ('nan', -0.014755669981241226), ('[SEP]', -0.06062338501214981)]


...

274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('connect', -1.0), ('www', -0.9168021082878113), ('.', -0.2871396541595459), ('google', -0.5681913495063782), ('.', -0.0666731595993042), ('com', -0.11801663786172867), (':', -0.0048239100724458694), ('80', -0.0), ('nan', -0.03999503329396248), ('[SEP]', -0.1866270750761032)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('patch', -0.20963026583194733), ('/', -1.0), ('r4', -0.053375665098428726), ('##ac', -0.05918553099036217), ('##oj', -0.006183848716318607), ('##rv', -0.023152673617005348), ('##8e', -0.011873400770127773), ('"', -0.036327142268419266), ('c8', -0.007140398491173983), ('##ti', -0.004522138740867376), ('##k', -0.027807485312223434), ('##q', -0.004665428306907415), ('##2c', -0.01119755394756794), ('##fg', -0.006727559957653284), ('##ux', -0.002427218481898308), ('##e8', -0.00520274369046092), ('##1', -0.019150065258145332), ('"', -0.009578079916536808), (':', -0.038945626467466354), ('"', -0.008398530073463917), ('1', -0.01082494854927063), ('##if', -0.003014650894328952), ('##uo', -0.0004600445681717247), ('##e8', -0.004471817519515753), ('##rq', -0.000683087797369808), ('##ds', -0.0024580026511102915), ('##ake', -0.0), ('##t', -0.0036917550023645163), ('"', -0.014788530766963959), ('[SEP]', -0.03049321286380291)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('connect', -1.0), ('www', -0.9168021082878113), ('.', -0.2871396541595459), ('google', -0.5681913495063782), ('.', -0.0666731595993042), ('com', -0.11801663786172867), (':', -0.0048239100724458694), ('80', -0.0), ('nan', -0.03999503329396248), ('[SEP]', -0.1866270750761032)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('put', -0.9791619777679443), ('/', -1.0), ('ix', -0.08273659646511078), ('##q6', -0.0228174589574337), ('##1', -0.0672094076871872), ('##piv', -0.014229823835194111), ('##7', -0.03370952978730202), ('##k', -0.02036290615797043), ('"', -0.007158305030316114), ('b8', -0.022945277392864227), ('##1b', -0.006627115420997143), ('##aj', -0.011366990394890308), ('##hf', -0.03381798788905144), ('##x', -0.004865419119596481), ('##z', -0.006711229216307402), ('##gw', -0.01087653636932373), ('##ams', -0.05934922397136688), ('"', -0.016691608354449272), (':', -0.017525674775242805), ('"', -0.00762561708688736), ('lb', -0.011521300300955772), ('##4j', -0.017765715718269348), ('##3', -0.004077946301549673), ('##jl', -0.0), ('##x', -0.0022070701234042645), ('##3z', -0.0007413673447445035), ('##p', -0.007973326370120049), ('##g', -0.007647003047168255), ('##9', -0.03280401974916458), ('##p', -0.006662696599960327), ('##7', -0.02269624173641205), ('"', -0.004

274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('patch', -1.0), ('/', -0.7912320494651794), ('icons', -0.2972092032432556), ('/', -0.2923244833946228), ('r6', -0.07405194640159607), ('##b20', -0.01536211185157299), ('##g2', -0.009238539263606071), ('##2v', -0.011657169088721275), ('##3', -0.0259185042232275), ('"', -0.016360972076654434), ('kj', -0.007351222448050976), ('##0', -0.0035346290096640587), ('##je', -0.0019911073613911867), ('##mpi', -0.03688071295619011), ('##ch', -0.018665554001927376), ('##nn', -0.024052100256085396), ('##6', -0.0023506288416683674), ('##ku', -0.015066763386130333), ('"', -0.013140406459569931), (':', -0.09009642153978348), ('"', -0.010267390869557858), ('ji', -0.0044146934524178505), ('##fp', -0.0030581094324588776), ('##g', -0.002502520801499486), ('##vm', -0.009682804346084595), ('##xa', -0.009823350235819817), ('##ez', -0.02621554769575596), ('##xq', -0.0), ('##s', -0.004306423477828503), ('##v', -0.012941870838403702), ('"', -0.009529374539852142), ('[S

In [24]:
sqli = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/66.csv')
for index, row in sqli.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.15738072991371155), ('/', -0.05353615805506706), ('blog', -0.02606026828289032), ('/', -0.06349692493677139), ('index', -0.02911604940891266), ('.', -0.030889704823493958), ('php', -0.016671251505613327), ('/', -0.051719214767217636), ('2020', -0.06795421242713928), ('/', -0.07117138803005219), ('04', -0.12365265935659409), ('%', -0.37315329909324646), ('27', -0.7016379833221436), ('+', -0.6644013524055481), ('and', -0.40268048644065857), ('+', -0.9194818735122681), ('0', -0.29926127195358276), ('+', -0.9736800193786621), ('in', -0.20761775970458984), ('+', -0.9741125106811523), ('%', -0.3848530054092407), ('28', -0.3954559564590454), ('##select', -0.0572182796895504), ('+', -0.6685777306556702), ('sleep', -0.13022936880588531), ('%', -0.22528265416622162), ('2815', -0.14102399349212646), ('%', -0.2806703448295593), ('29', -0.31744158267974854), ('+', -1.0), ('%', -0.3149096369743347), ('29', -0.8260104656219482), ('+', -0.722462654113769

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.20560023188591003), ('/', -0.01978333853185177), ('blog', -0.030193638056516647), ('/', -0.03337240219116211), ('index', -0.005627643316984177), ('.', -0.022949326783418655), ('php', -0.010694734752178192), ('%', -0.30195116996765137), ('2522', -0.14585062861442566), ('%', -0.10286436229944229), ('2b', -0.1429659128189087), ('##and', -0.016479745507240295), ('%', -0.103005550801754), ('2b', -0.3884356617927551), ('%', -0.08012640476226807), ('2522', -0.004951578099280596), ('##1', -0.022677050903439522), ('%', -0.06871993094682693), ('2522', -0.021467158570885658), ('%', -0.03993070870637894), ('253', -0.006174004171043634), ('##d', -0.010012415237724781), ('%', -0.05887797474861145), ('2522', -0.005498006008565426), ('##2', -0.01874602399766445), ('%', -0.06818422675132751), ('2522', -0.021144280210137367), ('%', -0.04173790290951729), ('2b', -0.08417396992444992), ('-', -0.009504595771431923), ('-', -0.0154209453612566), ('%', -0.045653

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.14296168088912964), ('/', -0.07591188699007034), ('blog', -0.0376257486641407), ('/', -0.11308189481496811), ('index', -0.05436990037560463), ('.', -0.059636492282152176), ('php', -0.036607202142477036), ('/', -0.06248745694756508), ('2020', -0.07455231249332428), ('/', -0.11599796265363693), ('03', -0.19428880512714386), ('+', -0.8809371590614319), ('union', -0.2753763794898987), ('+', -0.8578999638557434), ('all', -0.2528288662433624), ('+', -0.8137547969818115), ('select', -0.1324174404144287), ('+', -1.0), ('null', -0.4458998739719391), ('%', -0.14962421357631683), ('2c', -0.10173935443162918), ('##null', -0.07412834465503693), ('%', -0.13132064044475555), ('2c', -0.08991888165473938), ('##null', -0.050247542560100555), ('%', -0.10724455863237381), ('2c', -0.049608077853918076), ('##null', -0.022559629753232002), ('%', -0.046476807445287704), ('2c', -0.03663387894630432), ('##null', -0.021443786099553108), ('%', -0.05148336663842201),

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.01719510927796364), ('/', -0.008755428716540337), ('blog', -0.0017921486869454384), ('/', -0.008808854967355728), ('index', -0.0004289057687856257), ('.', -0.0025110209826380014), ('php', -0.0022432010155171156), ('%', -0.25084489583969116), ('26', -0.06408451497554779), ('##sl', -0.002121193800121546), ('##ee', -0.00037128201802261174), ('##p', -0.003743886947631836), ('%', -0.13520453870296478), ('24', -0.027504071593284607), ('##mc', -0.011943130753934383), ('+', -1.0), ('15', -0.20697802305221558), ('%', -0.07239703088998795), ('26', -0.14004452526569366), ('/', -0.010817253962159157), ('2020', -0.0009590159170329571), ('/', -0.0038185047451406717), ('04', -0.0014555160887539387), ('/', -0.002867388539016247), ('04', -0.0002354582102270797), ('/', -0.0011329917469993234), ('page', -0.0), ('/', -0.00043258501682430506), ('2', -0.0005525752785615623), ('[SEP]', -6.341482367133722e-05)]


...

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.13980944454669952), ('/', -0.06623139977455139), ('blog', -0.05242462083697319), ('%', -0.3718831539154053), ('22', -0.5448362231254578), ('+', -0.6890025734901428), ('or', -0.17171844840049744), ('+', -0.772773265838623), ('0', -0.2656985819339752), ('+', -0.8036985993385315), ('in', -0.13750167191028595), ('+', -0.9355815649032593), ('%', -0.3473612666130066), ('28', -0.49525001645088196), ('##select', -0.05861354619264603), ('+', -0.771817147731781), ('sleep', -0.13770823180675507), ('%', -0.1785418540239334), ('2815', -0.16771118342876434), ('%', -0.22620883584022522), ('29', -0.45992299914360046), ('+', -1.0), ('%', -0.3358713388442993), ('29', -0.6818915009498596), ('+', -0.5805495977401733), ('-', -0.07137605547904968), ('-', -0.07911735773086548), ('+', -0.6785150170326233), ('/', -0.04213042929768562), ('wp', -0.0177910253405571), ('-', -0.01028414722532034), ('content', -0.01842777244746685), ('/', -0.009767689742147923), ('uplo

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.009219634346663952), ('/', -0.007545990403741598), ('blog', -0.003943752497434616), ('%', -0.1729106605052948), ('26', -0.05379617214202881), ('##sl', -0.0015721877571195364), ('##ee', -0.0), ('##p', -0.0011682118056342006), ('%', -0.051144108176231384), ('24', -0.016797764226794243), ('##mc', -0.008693719282746315), ('+', -1.0), ('15', -0.1297583431005478), ('%', -0.06954305619001389), ('26', -0.03686060383915901), ('/', -0.008454634808003902), ('wp', -0.000729091465473175), ('-', -0.0005946838646195829), ('includes', -0.0005628477083519101), ('/', -0.002401854610070586), ('css', -0.00046863729949109256), ('[SEP]', -0.0007909067207947373)]


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.19591164588928223), ('/', -0.07454049587249756), ('blog', -0.03759339824318886), ('/', -0.08523110300302505), ('index', -0.04479046165943146), ('.', -0.037612028419971466), ('php', -0.052327584475278854), ('%', -0.44276827573776245), ('27', -0.5998181700706482), ('+', -0.7305210828781128), ('or', -0.22752422094345093), ('+', -0.9607701301574707), ('0', -0.36008399724960327), ('+', -0.8908411860466003), ('in', -0.18162737786769867), ('+', -0.9692710041999817), ('%', -0.4055599272251129), ('28', -0.6125355958938599), ('##select', -0.08658056706190109), ('+', -0.6092802286148071), ('sleep', -0.15067428350448608), ('%', -0.22448399662971497), ('2815', -0.1837596744298935), ('%', -0.33426377177238464), ('29', -0.580622673034668), ('+', -0.9224551916122437), ('%', -0.30009081959724426), ('29', -0.5363298654556274), ('+', -0.6599957942962646), ('-', -0.11139752715826035), ('-', -0.11365000903606415), ('+', -1.0), ('/', -0.04117294400930405), ('c

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.029656676575541496), ('/', -0.0032985438592731953), ('blog', -0.0022006859071552753), ('/', -0.0025616344064474106), ('index', -0.0), ('.', -0.0002633468247950077), ('php', -0.00024903786834329367), ('/', -0.002524732379242778), ('search', -0.003204710315912962), ('/', -0.00189593608956784), ('percentage', -0.0016563169192522764), ('%', -0.08182022720575333), ('22', -1.0), ('[SEP]', -0.0031006040517240763)]


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.25694283843040466), ('/', -0.07076378911733627), ('blog', -0.016877315938472748), ('/', -0.07266837358474731), ('index', -0.02030446194112301), ('.', -0.022353073582053185), ('php', -0.019840436056256294), ('/', -0.029434019699692726), ('2020', -0.03082340955734253), ('/', -0.05220410227775574), ('03', -0.03504707291722298), ('/', -0.04901641979813576), ('23', -0.015097076073288918), ('/', -0.030041730031371117), ('fu', -0.0009184426162391901), ('##ga', -0.0007472746074199677), ('-', -0.002377171302214265), ('aut', -0.0004715288523584604), ('-', -0.0013157190987840295), ('rec', -0.001843547448515892), ('##usa', -0.0), ('##nd', -0.0016653272323310375), ('##ae', -0.0013702037977054715), ('-', -0.0024730104487389326), ('sed', -0.002151161665096879), ('-', -0.0009566516964696348), ('dol', -0.0006747602019459009), ('##or', -0.004249394405633211), ('-', -0.00493635842576623), ('qu', -0.004616645630449057), ('##ia', -0.027866967022418976), ('%',

In [25]:
OS_Command_Injection = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/88.csv')
for index, row in OS_Command_Injection.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


88 - OS Command Injection
[('[CLS]', -0.0), ('post', -0.01849554106593132), ('/', -0.0026866879779845476), ('cgi', -0.005765775218605995), ('-', -0.0029653592500835657), ('bin', -0.004306869115680456), ('/', -0.006328185088932514), ('view', -0.0037722671404480934), ('##log', -0.00222058966755867), ('.', -0.005561864469200373), ('asp', -0.01962307095527649), ('remote', -0.005088988225907087), ('_', -0.019243044778704643), ('submit', -0.00814630277454853), ('_', -0.007901571691036224), ('flag', -0.009425277821719646), ('=', -0.10565146803855896), ('1', -0.04542504623532295), ('&', -0.025636136531829834), ('remote', -0.007573351263999939), ('_', -0.0078077297657728195), ('syslog', -0.003205168293789029), ('_', -0.010615022853016853), ('flag', -0.0032477707136422396), ('=', -0.039825208485126495), ('1', -0.019617602229118347), ('&', -0.011351905763149261), ('remote', -0.0036188396625220776), ('##sys', -0.0015527738723903894), ('##logs', -0.0013154092011973262), ('##upport', -0.001142556080

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.0), ('/', -0.020952893421053886), ('<', -1.0), ('?', -0.5827596783638), ('xml', -0.014208076521754265), ('version', -0.03598826751112938), ('=', -0.09698249399662018), ('"', -0.24595753848552704), ('1', -0.10373520851135254), ('.', -0.04813437536358833), ('0', -0.04151386395096779), ('"', -0.06481698155403137), ('encoding', -0.01915672980248928), ('=', -0.07799262553453445), ('"', -0.06154974177479744), ('utf', -0.05509139597415924), ('-', -0.008522393181920052), ('8', -0.016774777323007584), ('"', -0.0805637389421463), ('?', -0.28660210967063904), ('>', -0.31577256321907043), ('[SEP]', -0.017902454361319542)]


126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.06208787113428116), ('/', -0.01571447215974331), ('tiki', -0.0), ('-', -0.01659424975514412), ('list', -0.01229941938072443), ('##mov', -0.002058229874819517), ('##ies', -0.013927998021245003), ('.', -0.06155359372496605), ('php', -0.01807723008096218), ('?', -0.04257885366678238), ('movie', -0.009208067320287228), ('=', -0.12810973823070526), ('.', -0.6637564897537231), ('.', -1.0), ('/', -0.19916369020938873), ('.', -0.5223081707954407), ('.', -0.8217223882675171), ('/', -0.2471015751361847), ('.', -0.6290067434310913), ('.', -0.8563341498374939), ('/', -0.2299940139055252), ('.', -0.3991623520851135), ('.', -0.5931997895240784), ('/', -0.17833435535430908), ('.', -0.5376016497612), ('.', -0.7271838188171387), ('/', -0.21561723947525024), ('.', -0.4943610429763794), ('.', -0.5986075401306152), ('/', -0.11180572211742401), ('etc', -0.041410356760025024), ('/', -0.016115980222821236), ('passwd', -0.030284782871603966), ('%', -0.01138055

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.2775481045246124), ('/', -0.0), ('?', -0.6789310574531555), ('p4', -0.018036892637610435), ('##yl', -0.044904302805662155), ('##04', -0.0009086051140911877), ('##d', -0.01101984828710556), ('=', -0.369293749332428), ('.', -0.6039919853210449), ('.', -1.0), ('/', -0.20946326851844788), ('.', -0.6326655745506287), ('.', -0.7745659351348877), ('/', -0.18500526249408722), ('.', -0.639371395111084), ('.', -0.892456591129303), ('/', -0.20683395862579346), ('.', -0.5585611462593079), ('.', -0.6456490159034729), ('/', -0.2008369415998459), ('.', -0.5177059769630432), ('.', -0.6135354042053223), ('/', -0.18146586418151855), ('.', -0.5041964650154114), ('.', -0.6222597360610962), ('/', -0.18446582555770874), ('.', -0.5459839701652527), ('.', -0.5802748203277588), ('/', -0.15282323956489563), ('.', -0.3927800953388214), ('.', -0.4237358868122101), ('/', -0.13392513990402222), ('.', -0.359587162733078), ('.', -0.45864254236221313), ('/', -0.1484040

...

88 - OS Command Injection
[('[CLS]', -0.0), ('get', -0.010577667504549026), ('/', -0.04135557636618614), ('index', -0.06962589919567108), ('.', -0.1296710968017578), ('php', -0.0), ('?', -0.15274661779403687), ('s', -0.19857092201709747), ('=', -0.2418317198753357), ('/', -0.13105949759483337), ('module', -0.08342644572257996), ('/', -0.0949031263589859), ('action', -0.040072932839393616), ('/', -0.05904737487435341), ('param1', -0.036567382514476776), ('/', -0.11526443809270859), ('$', -0.13930076360702515), ('{', -1.0), ('@', -0.21817240118980408), ('die', -0.18108539283275604), ('(', -0.08673873543739319), ('sha1', -0.11692282557487488), ('(', -0.117243692278862), ('xyz', -0.046723343431949615), ('##t', -0.021906426176428795), (')', -0.35786113142967224), (')', -0.5671238303184509), ('}', -0.2552763819694519), ('[SEP]', -0.04671405255794525)]


126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.10418971627950668), ('/', -0.05287793278694153), ('blog', -0.03874354809522629), ('/', -0.08096940070390701), ('index', -0.16196440160274506), ('.', -0.2552357614040375), ('php', -0.3056555390357971), ('/', -0.07393989711999893), ('my', -0.19893789291381836), ('-', -0.050350409001111984), ('account', -0.2163139432668686), ('/', -0.03273048624396324), ('edit', -0.04893038421869278), ('-', -0.038590751588344574), ('password', -0.22453266382217407), ('/', -0.05400882661342621), ('password', -0.24879755079746246), ('_', -0.09629634767770767), ('current', -0.1598009616136551), ('=', -1.0), ('%', -0.296653687953949), ('2f', -0.36959266662597656), ('##etc', -0.17656159400939941), ('%', -0.2128576785326004), ('2f', -0.31236162781715393), ('##pass', -0.027805443853139877), ('##wd', -0.047533247619867325), ('&', -0.12880410254001617), ('password', -0.1974402517080307), ('_', -0.07301001250743866), ('1', -0.10927014797925949), ('=', -0.4325678646

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.12703992426395416), ('/', -0.053086649626493454), ('blog', -0.029551459476351738), ('/', -0.08780251443386078), ('index', -0.1438053846359253), ('.', -0.23923465609550476), ('php', -0.22357884049415588), ('/', -0.05824818089604378), ('my', -0.17437362670898438), ('-', -0.04237528517842293), ('account', -0.20076709985733032), ('/', -0.03256886079907417), ('edit', -0.0322544239461422), ('-', -0.03515918180346489), ('password', -0.17159965634346008), ('/', -0.04659461975097656), ('password', -0.20538601279258728), ('_', -0.061968278139829636), ('current', -0.09571052342653275), ('=', -1.0), ('.', -0.6432002186775208), ('.', -0.7324309349060059), ('%', -0.3141397535800934), ('2f', -0.2483212798833847), ('.', -0.43364405632019043), ('.', -0.4924464821815491), ('%', -0.2085765302181244), ('2f', -0.1445421576499939), ('.', -0.3108040988445282), ('.', -0.41761571168899536), ('%', -0.13400773704051971), ('2f', -0.17142240703105927), ('.', -0.23

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.07970749586820602), ('/', -0.050929244607686996), ('blog', -0.03972526267170906), ('/', -0.0945901945233345), ('index', -0.16668370366096497), ('.', -0.30456218123435974), ('php', -0.26185718178749084), ('/', -0.05950278043746948), ('my', -0.1893988698720932), ('-', -0.0550798699259758), ('account', -0.25894010066986084), ('/', -0.032891374081373215), ('edit', -0.03887929767370224), ('-', -0.04091044142842293), ('password', -0.23458319902420044), ('/', -0.04868505150079727), ('password', -0.2624102234840393), ('_', -0.08077444136142731), ('current', -0.12340900301933289), ('=', -1.0), ('%', -0.22858364880084991), ('2f', -0.3978482782840729), ('.', -0.7748644351959229), ('.', -0.8017663955688477), ('%', -0.3281328082084656), ('2f', -0.3286954164505005), ('.', -0.45880454778671265), ('.', -0.5672827959060669), ('%', -0.18915720283985138), ('2f', -0.28318172693252563), ('.', -0.322021484375), ('.', -0.46369805932044983), ('%', -0.13819919

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.08640267699956894), ('/', -0.04332052171230316), ('blog', -0.02224801667034626), ('/', -0.09499821811914444), ('index', -0.08109906315803528), ('.', -0.17829765379428864), ('php', -0.22115816175937653), ('/', -0.04615506902337074), ('my', -0.08289101719856262), ('-', -0.016422927379608154), ('account', -0.086465023458004), ('/', -0.019571028649806976), ('edit', -0.012380184605717659), ('-', -0.012326392345130444), ('password', -0.08013132959604263), ('/', -0.03281625360250473), ('password', -0.08745444566011429), ('_', -0.057909656316041946), ('current', -0.1253093034029007), ('=', -1.0), ('etc', -0.16414563357830048), ('%', -0.21743276715278625), ('2f', -0.265470951795578), ('##pass', -0.01261981576681137), ('##wd', -0.014895206317305565), ('&', -0.06485605239868164), ('password', -0.06494981050491333), ('_', -0.03533302992582321), ('1', -0.05400710180401802), ('=', -0.36476457118988037), ('q', -0.08826959878206253), ('##lh', -0.00525

In [26]:
for index, row in normal.iterrows():
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0



    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]

    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
        # generate an explanation for the input
        expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
        # normalize scores
        expl = (expl - expl.min()) / (expl.max() - expl.min())
        expl *= (-1)
        tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
        print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
        vis_data_records = [visualization.VisualizationDataRecord(
                                        expl,
                                        output[0][classification],
                                        classification,
                                        true_class,
                                        true_class,
                                        1,
                                        tokens,
                                        1)]
        visualization.visualize_text(vis_data_records)
    else:
        count += 1
print("Acc: ",count/(index + 1))

[('[CLS]', -0.0), ('get', -0.2137824296951294), ('/', -0.010729064233601093), ('blog', -0.040987640619277954), ('/', -0.001939126173965633), ('xmlrpc', -0.04450560733675957), ('.', -0.0), ('php', -0.08688294142484665), ('?', -1.0), ('rs', -0.36760661005973816), ('##d', -0.7329966425895691), ('[SEP]', -0.010899742133915424)]


[('[CLS]', -0.0), ('get', -0.029228514060378075), ('/', -0.004831802099943161), ('blog', -0.0), ('/', -0.00756204966455698), ('wp', -0.002608509734272957), ('-', -0.016862530261278152), ('includes', -0.0040654344484210014), ('/', -0.0043479823507368565), ('css', -0.0204672459512949), ('/', -0.0017944276332855225), ('dash', -0.01247056107968092), ('##icon', -0.030848445370793343), ('##s', -0.02079118974506855), ('.', -0.13724173605442047), ('min', -0.12369417399168015), ('.', -0.07823312282562256), ('css', -0.2251276969909668), ('?', -1.0), ('ver', -0.0770794004201889), ('=', -0.32453060150146484), ('4', -0.06609314680099487), ('.', -0.03790244460105896), ('9', -0.06944720447063446), ('.', -0.03615601733326912), ('5', -0.08088882267475128), ('[SEP]', -0.04766126349568367)]


[('[CLS]', -0.0), ('get', -0.2571159303188324), ('/', -0.02063479833304882), ('blog', -0.05324934422969818), ('/', -0.06468328833580017), ('wp', -0.0), ('-', -0.032555900514125824), ('includes', -0.023441120982170105), ('/', -0.011537544429302216), ('css', -0.025747880339622498), ('/', -0.010731389746069908), ('admin', -0.00046521297190338373), ('-', -0.014058859087526798), ('bar', -0.017920006066560745), ('.', -0.15717922151088715), ('min', -0.13296790421009064), ('.', -0.09917493909597397), ('css', -0.22757704555988312), ('?', -1.0), ('ver', -0.10764351487159729), ('=', -0.35139697790145874), ('4', -0.0729081779718399), ('.', -0.036652565002441406), ('9', -0.10258902609348297), ('.', -0.037059832364320755), ('5', -0.10684904456138611), ('[SEP]', -0.04242324456572533)]


[('[CLS]', -0.0), ('get', -0.3537708520889282), ('/', -0.03755148500204086), ('blog', -0.07143796980381012), ('/', -0.11810234189033508), ('wp', -0.005461920518428087), ('-', -0.044129591435194016), ('content', -0.008483385667204857), ('/', -0.023198721930384636), ('plugins', -0.02252933569252491), ('/', -0.020952580496668816), ('user', -0.00931086577475071), ('-', -0.02956169843673706), ('registration', -0.004967574030160904), ('/', -0.018854564055800438), ('assets', -0.0), ('/', -0.015782281756401062), ('css', -0.0037851466331630945), ('/', -0.02258450537919998), ('user', -0.009574001654982567), ('-', -0.046273794025182724), ('registration', -0.004868329036980867), ('.', -0.04189752787351608), ('css', -0.05213167518377304), ('?', -1.0), ('ver', -0.06967555731534958), ('=', -0.8870480060577393), ('1', -0.07770659029483795), ('.', -0.0829046443104744), ('8', -0.09084473550319672), ('.', -0.04214709997177124), ('2', -0.0682528093457222), ('.', -0.056262362748384476), ('1', -0.0544879883

[('[CLS]', -0.0), ('get', -0.5241652727127075), ('/', -0.07417524605989456), ('blog', -0.15248778462409973), ('/', -0.13281533122062683), ('wp', -0.007465875241905451), ('-', -0.0553317666053772), ('includes', -0.014348281547427177), ('/', -0.04631391540169716), ('js', -0.03400522097945213), ('/', -0.03816724196076393), ('jquery', -0.0), ('/', -0.04247157275676727), ('jquery', -0.001262990408577025), ('.', -0.07930437475442886), ('js', -0.06930717825889587), ('?', -1.0), ('ver', -0.08333922177553177), ('=', -0.4712315499782562), ('1', -0.07032203674316406), ('.', -0.11169091612100601), ('12', -0.20907112956047058), ('.', -0.09994978457689285), ('4', -0.09222918748855591), ('[SEP]', -0.03873004391789436)]


...

[('[CLS]', -0.0), ('get', -0.11420279741287231), ('/', -0.017319032922387123), ('blog', -0.02553768828511238), ('/', -0.011367205530405045), ('load', -0.06033217906951904), ('-', -0.004310158081352711), ('styles', -0.002186040859669447), ('.', -0.0035836435854434967), ('php', -0.03182845190167427), ('?', -0.2523825168609619), ('c', -0.09532972425222397), ('=', -0.2238454669713974), ('0', -0.12205792218446732), ('&', -1.0), ('dir', -0.011152584105730057), ('=', -0.050158992409706116), ('lt', -0.019550569355487823), ('##r', -0.00795751716941595), ('&', -0.1567230373620987), ('load', -0.014090151526033878), ('%', -0.1391952633857727), ('5b', -0.04436860606074333), ('%', -0.12186737358570099), ('5d', -0.04898109659552574), ('=', -0.017761671915650368), ('dash', -0.007360295858234167), ('##icon', -6.417515396606177e-05), ('##s', -0.0022573021706193686), (',', -0.003776544239372015), ('buttons', -0.002172803273424506), (',', -0.0038372441194951534), ('forms', -0.0037639932706952095), (',', -

[('[CLS]', -0.0), ('get', -0.11420279741287231), ('/', -0.017319032922387123), ('blog', -0.02553768828511238), ('/', -0.011367205530405045), ('load', -0.06033217906951904), ('-', -0.004310158081352711), ('styles', -0.002186040859669447), ('.', -0.0035836435854434967), ('php', -0.03182845190167427), ('?', -0.2523825168609619), ('c', -0.09532972425222397), ('=', -0.2238454669713974), ('0', -0.12205792218446732), ('&', -1.0), ('dir', -0.011152584105730057), ('=', -0.050158992409706116), ('lt', -0.019550569355487823), ('##r', -0.00795751716941595), ('&', -0.1567230373620987), ('load', -0.014090151526033878), ('%', -0.1391952633857727), ('5b', -0.04436860606074333), ('%', -0.12186737358570099), ('5d', -0.04898109659552574), ('=', -0.017761671915650368), ('dash', -0.007360295858234167), ('##icon', -6.417515396606177e-05), ('##s', -0.0022573021706193686), (',', -0.003776544239372015), ('buttons', -0.002172803273424506), (',', -0.0038372441194951534), ('forms', -0.0037639932706952095), (',', -

[('[CLS]', -0.0), ('get', -0.15794998407363892), ('/', -0.03460002690553665), ('blog', -0.05648922547698021), ('/', -0.03151799738407135), ('wp', -0.027064248919487), ('-', -0.018459562212228775), ('admin', -0.03622986748814583), ('/', -0.006314775440841913), ('?', -0.08179350942373276), ('c', -0.08322462439537048), ('=', -0.295854389667511), ('0', -0.06705822795629501), ('&', -1.0), ('dir', -0.015026157721877098), ('=', -0.0421619638800621), ('lt', -0.01633298583328724), ('##r', -0.011385541409254074), ('&', -0.12082735449075699), ('load', -0.018024403601884842), ('%', -0.11132005602121353), ('5b', -0.03451000154018402), ('%', -0.1872403770685196), ('5d', -0.03434433788061142), ('=', -0.0358411967754364), ('dash', -0.006552283186465502), ('##icon', -0.0002037504455074668), ('##s', -0.0035693731624633074), (',', -0.0061895898543298244), ('buttons', -0.001208604546263814), (',', -0.005088005680590868), ('forms', -0.002789122750982642), (',', -0.009493579156696796), ('l10n', -0.001525808

[('[CLS]', -0.0), ('get', -0.18194198608398438), ('/', -0.04349697381258011), ('blog', -0.08066777884960175), ('/', -0.04252604395151138), ('wp', -0.058992739766836166), ('-', -0.05102280527353287), ('admin', -0.03776485100388527), ('?', -0.298069566488266), ('c', -0.03545066714286804), ('=', -0.24061615765094757), ('0', -0.0955599918961525), ('&', -1.0), ('dir', -0.03333472087979317), ('=', -0.1012549102306366), ('lt', -0.033469051122665405), ('##r', -0.011864891275763512), ('&', -0.2650316059589386), ('load', -0.06583169847726822), ('%', -0.18075864017009735), ('5b', -0.09823072701692581), ('%', -0.19536523520946503), ('5d', -0.039511676877737045), ('=', -0.07781476527452469), ('dash', -0.013275534845888615), ('##icon', -0.0), ('##s', -0.00712352292612195), (',', -0.12640051543712616), ('buttons', -0.01206760760396719), (',', -0.08914756029844284), ('forms', -0.01383753027766943), (',', -0.12073992937803268), ('l10n', -0.0019306109752506018), (',', -0.11094771325588226), ('login', -0

Acc:  0.9673336055532871


In [27]:
for index, row in sqli.iterrows():
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0



    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]

    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "66 - SQL Injection":
        # generate an explanation for the input
        expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
        # normalize scores
        expl = (expl - expl.min()) / (expl.max() - expl.min())
        expl *= (-1)
        tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
        print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
        vis_data_records = [visualization.VisualizationDataRecord(
                                        expl,
                                        output[0][classification],
                                        classification,
                                        true_class,
                                        true_class,
                                        1,
                                        tokens,
                                        1)]
        visualization.visualize_text(vis_data_records)
    else:
        count += 1
print("Acc: ",count/(index + 1))

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


[('[CLS]', -0.0), ('get', -0.43230924010276794), ('/', -0.02974393591284752), ('blog', -0.0855647474527359), ('/', -0.06703054904937744), ('wp', -0.0), ('-', -0.08063894510269165), ('includes', -0.0011981995776295662), ('/', -0.018289344385266304), ('js', -0.01716449297964573), ('/', -0.006811466999351978), ('api', -0.006440745200961828), ('-', -0.024395011365413666), ('request', -0.005273896269500256), ('.', -0.11031921952962875), ('min', -0.02546391263604164), ('.', -0.06575027108192444), ('js', -0.0804809033870697), ('?', -1.0), ('ver', -0.0584024116396904), ('=', -0.23275235295295715), ('4', -0.05271754041314125), ('.', -0.08336340636014938), ('9', -0.0704009160399437), ('.', -0.06421583145856857), ('5', -0.06414199620485306), ('[SEP]', -0.027331851422786713)]


[('[CLS]', -0.0), ('get', -0.6827594041824341), ('/', -0.06577295809984207), ('blog', -0.10221706330776215), ('/', -0.19420164823532104), ('wp', -0.0032104391139000654), ('-', -0.017294054850935936), ('login', -0.013681056909263134), ('.', -0.05765479803085327), ('php', -0.1147167906165123), ('?', -1.0), ('_', -0.06934531778097153), ('wp', -0.02380032278597355), ('##non', -0.0025637613143771887), ('##ce', -0.023352069780230522), ('=', -0.2085520327091217), ('7d', -0.3393220603466034), ('##e0a', -0.0030335010960698128), ('##bc', -0.0), ('##dc', -0.005503940396010876), ('##2', -0.005073511507362127), ('&', -0.10649646818637848), ('action', -0.06485486030578613), ('=', -0.11977889388799667), ('logout', -0.09423119574785233), ('[SEP]', -0.02476470172405243)]


[('[CLS]', -0.0), ('get', -0.028996245935559273), ('/', -0.005041709169745445), ('blog', -0.0), ('/', -0.008769684471189976), ('wp', -0.003003210760653019), ('-', -0.021537350490689278), ('includes', -0.010264094918966293), ('/', -0.010032686404883862), ('js', -0.02086665667593479), ('/', -0.004750357009470463), ('backbone', -0.04445578530430794), ('.', -0.1086062639951706), ('min', -0.2170005887746811), ('.', -0.0380663238465786), ('js', -0.12280790507793427), ('?', -1.0), ('ver', -0.21907515823841095), ('=', -0.34050461649894714), ('1', -0.06054118275642395), ('.', -0.0407925583422184), ('2', -0.08471377193927765), ('.', -0.06263439357280731), ('3', -0.2001805156469345), ('[SEP]', -0.09721047431230545)]


[('[CLS]', -0.0), ('get', -0.5347815752029419), ('/', -0.056331511586904526), ('blog', -0.09431269019842148), ('/', -0.08812358975410461), ('wp', -0.02971373125910759), ('-', -0.12144630402326584), ('includes', -0.012211855500936508), ('/', -0.02156728506088257), ('js', -0.05004061385989189), ('/', -0.0166754350066185), ('plupload', -0.0), ('/', -0.02743884176015854), ('wp', -0.06782922148704529), ('-', -0.04969656467437744), ('plupload', -0.025597773492336273), ('.', -0.11199261993169785), ('min', -0.058571748435497284), ('.', -0.0965159460902214), ('js', -0.12877783179283142), ('?', -1.0), ('ver', -0.1148221492767334), ('=', -0.2733438313007355), ('4', -0.05891149118542671), ('.', -0.05923708528280258), ('9', -0.06565877050161362), ('.', -0.07233401387929916), ('5', -0.04124271869659424), ('[SEP]', -0.01191879715770483)]


...

[('[CLS]', -0.0), ('get', -0.029228514060378075), ('/', -0.004831802099943161), ('blog', -0.0), ('/', -0.00756204966455698), ('wp', -0.002608509734272957), ('-', -0.016862530261278152), ('includes', -0.0040654344484210014), ('/', -0.0043479823507368565), ('css', -0.0204672459512949), ('/', -0.0017944276332855225), ('dash', -0.01247056107968092), ('##icon', -0.030848445370793343), ('##s', -0.02079118974506855), ('.', -0.13724173605442047), ('min', -0.12369417399168015), ('.', -0.07823312282562256), ('css', -0.2251276969909668), ('?', -1.0), ('ver', -0.0770794004201889), ('=', -0.32453060150146484), ('4', -0.06609314680099487), ('.', -0.03790244460105896), ('9', -0.06944720447063446), ('.', -0.03615601733326912), ('5', -0.08088882267475128), ('[SEP]', -0.04766126349568367)]


[('[CLS]', -0.0), ('get', -0.6617807745933533), ('/', -0.08659633994102478), ('blog', -0.15191589295864105), ('/', -0.17280925810337067), ('wp', -0.0), ('-', -0.2618328630924225), ('includes', -0.00393541669473052), ('/', -0.09708454459905624), ('js', -0.019968068227171898), ('/', -0.04709058254957199), ('utils', -0.04372159764170647), ('.', -0.33346185088157654), ('min', -0.15619607269763947), ('.', -0.20281565189361572), ('js', -0.12673023343086243), ('?', -1.0), ('ver', -0.13002634048461914), ('=', -0.22350086271762848), ('4', -0.046102624386548996), ('.', -0.3052712082862854), ('9', -0.05878481641411781), ('.', -0.26457104086875916), ('5', -0.0975102037191391), ('[SEP]', -0.011590242385864258)]


[('[CLS]', -0.0), ('post', -0.14139457046985626), ('/', -0.04389045014977455), ('blog', -0.03290974721312523), ('/', -0.06351637840270996), ('index', -0.0718790665268898), ('.', -0.0880056843161583), ('php', -0.21402977406978607), ('/', -0.04422008991241455), ('my', -0.129408061504364), ('-', -0.04133278876543045), ('account', -0.1376885175704956), ('/', -0.025263160467147827), ('edit', -0.05887637659907341), ('-', -0.014222990721464157), ('profile', -0.07990996539592743), ('/', -0.06200026720762253), ('username', -0.19189034402370453), ('=', -0.5366590619087219), ('eager', -0.08056160062551498), ('##che', -0.0271346066147089), ('##ese', -0.03993627801537514), ('##1', -0.15977823734283447), ('&', -0.11453951895236969), ('password', -0.20332397520542145), ('=', -0.25295141339302063), ('rv', -0.12095474451780319), ('##ku', -0.011158655397593975), ('##n', -0.023719392716884613), ('##4', -0.09326126426458359), ('&', -0.0664006844162941), ('user', -0.08724268525838852), ('-', -0.00177695578

[('[CLS]', -0.0), ('get', -0.24866582453250885), ('/', -0.03087497130036354), ('blog', -0.03370094671845436), ('/', -0.0675191730260849), ('wp', -0.003373926505446434), ('-', -0.03379766270518303), ('content', -0.01312539353966713), ('/', -0.019261591136455536), ('themes', -0.001705962116830051), ('/', -0.021252712234854698), ('twenty', -0.0), ('##sevent', -0.001784082967787981), ('##een', -0.0071813385002315044), ('/', -0.01953706704080105), ('assets', -0.0018613003194332123), ('/', -0.01569051668047905), ('js', -0.01581849530339241), ('/', -0.017456257715821266), ('navigation', -0.006240337621420622), ('.', -0.03310292959213257), ('js', -0.037180934101343155), ('?', -1.0), ('ver', -0.08894484490156174), ('=', -0.6249113082885742), ('1', -0.10193420201539993), ('.', -0.038239698857069016), ('0', -0.10559772700071335), ('[SEP]', -0.07831945270299911)]


Acc:  1.927437641723356
